### **<font size=5> 🏷 Recognize Anything:** A Strong Image Tagging Model & **Tag2Text:** Guiding Vision-Language Model via Image Tagging </font>

Official PyTorch Implementation of the <a href="https://recognize-anything.github.io/">Recognize Anything Model (RAM)</a> and the <a href="https://tag2text.github.io/">Tag2Text Model</a>.

- RAM is an image tagging model, which can recognize any common category with high accuracy.
- Tag2Text is a vision-language model guided by tagging, which can support caption, retrieval and tagging.




In [1]:
#@title Import dependencies
import ipywidgets as widgets
from IPython.display import clear_output, display, Image
import os

In [2]:
#@title Clone the repository
!git clone https://github.com/xinyu1205/recognize-anything.git
%cd recognize-anything

Cloning into 'Recognize_Anything-Tag2Text'...
remote: Enumerating objects: 398, done.
remote: Counting objects: 100% (234/234), done.
remote: Compressing objects: 100% (120/120), done.
remote: Total 398 (delta 145), reused 177 (delta 113), pack-reused 164
Receiving objects: 100% (398/398), 9.24 MiB | 17.42 MiB/s, done.
Resolving deltas: 100% (203/203), done.
/content/Recognize_Anything-Tag2Text


In [3]:
#@title Install dependencies
!pip install timm transformers fairscale pycocoevalcap

clear_output()

In [4]:
# Download checkpoints
model_widget = widgets.Dropdown(
    options=["RAM", "Tag2Text"],
    value="RAM",
    description="Select mdoel:"
)
display(model_widget)

Dropdown(description='Select mdoel:', options=('RAM', 'Tag2Text'), value='RAM')

In [5]:
model = model_widget.value

In [6]:
def download_checkpoints(model):
    print('You selected', model)
    if not os.path.exists('pretrained'):
        os.makedirs('pretrained')

    if model == "RAM":
        ram_weights_path = 'pretrained/ram_swin_large_14m.pth'
        if not os.path.exists(ram_weights_path):
            !wget https://huggingface.co/spaces/xinyu1205/Recognize_Anything-Tag2Text/resolve/main/ram_swin_large_14m.pth -O pretrained/ram_swin_large_14m.pth
        else:
            print("RAM weights already downloaded!")
    else:
        tag2text_weights_path = 'pretrained/tag2text_swin_14m.pth'
        if not os.path.exists(tag2text_weights_path):
            !wget https://huggingface.co/spaces/xinyu1205/Recognize_Anything-Tag2Text/resolve/main/tag2text_swin_14m.pth -O pretrained/tag2text_swin_14m.pth
        else:
            print("Tag2Text weights already downloaded!")

download_checkpoints(model)
print(model, 'weights are downloaded!')


You selected Tag2Text
--2023-06-18 14:45:59--  https://huggingface.co/spaces/xinyu1205/Recognize_Anything-Tag2Text/resolve/main/tag2text_swin_14m.pth
Resolving huggingface.co (huggingface.co)... 18.155.68.116, 18.155.68.38, 18.155.68.44, ...
Connecting to huggingface.co (huggingface.co)|18.155.68.116|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs.huggingface.co/repos/e6/78/e678f8565485a3f321b1180e4c7e1e18a89a9295028358eedffb98981b37e11a/4ce96f0ce98f940a6680d567f66a38ccc9ca8c4e638e5f5c5c2e881a0e3502ac?response-content-disposition=attachment%3B+filename*%3DUTF-8%27%27tag2text_swin_14m.pth%3B+filename%3D%22tag2text_swin_14m.pth%22%3B&Expires=1687358760&Policy=eyJTdGF0ZW1lbnQiOlt7IlJlc291cmNlIjoiaHR0cHM6Ly9jZG4tbGZzLmh1Z2dpbmdmYWNlLmNvL3JlcG9zL2U2Lzc4L2U2NzhmODU2NTQ4NWEzZjMyMWIxMTgwZTRjN2UxZTE4YTg5YTkyOTUwMjgzNThlZWRmZmI5ODk4MWIzN2UxMWEvNGNlOTZmMGNlOThmOTQwYTY2ODBkNTY3ZjY2YTM4Y2NjOWNhOGM0ZTYzOGU1ZjVjNWMyZTg4MWEwZTM1MDJhYz9yZXNwb25zZS1jb250ZW5

In [7]:
images_dir_widget = widgets.Text(value="images/demo", description="Images dir:")
display(images_dir_widget)

Text(value='images/demo', description='Images dir:')

In [8]:
images_dir = images_dir_widget.value

In [9]:
image_files = [f"{images_dir}/{file}" for file in sorted(os.listdir(images_dir)) if file.lower().endswith(('.jpg', '.jpeg', '.png'))]
image_path = image_files[0]

# Create dropdown widget
image_dropdown = widgets.Dropdown(
    options=image_files,
    description='Select Image:',
)

# Create image preview widget
image_preview = widgets.Output()

# Define function to update image preview
def update_preview(change):
    global image_path
    image_path = change.new
    with image_preview:
        image_preview.clear_output()
        display(Image(filename=image_path, width=400))

# Set the initial image preview
with image_preview:
    display(Image(filename=image_files[0], width=400))

# Attach the update function to the dropdown
image_dropdown.observe(update_preview, names='value')

# Display the widgets
display(image_dropdown, image_preview)

Dropdown(description='Select Image:', options=('images/demo/demo1.jpg', 'images/demo/demo2.jpg', 'images/demo/…

Output()

In [10]:
# Define the task and run inference
task_widget = widgets.Dropdown(
    options=["one image", "multiple images"],
    value="one image",
    description="Task:"
)
display(task_widget)

Dropdown(description='Task:', index=1, options=('one image', 'multiple images'), value='multiple images')

In [11]:
task = task_widget.value

In [12]:
print('You selected', model)
print('You selected', task)

def run_inference(model, task):
    if model == "Tag2Text" and task == "one image":
        !python inference_tag2text.py  --image {image_path} \
        --pretrained pretrained/tag2text_swin_14m.pth
    elif model == "Tag2Text" and task == "multiple images":
        !python batch_inference.py --image-dir {images_dir} \
        --pretrained pretrained/tag2text_swin_14m.pth --model-type tag2text
    elif model == "RAM" and task == "one image":
        !python inference_ram.py  --image {image_path} \
        --pretrained pretrained/ram_swin_large_14m.pth
    elif model == "RAM" and task == "multiple images":
        !python batch_inference.py --image-dir {images_dir} \
        --pretrained pretrained/ram_swin_large_14m.pth --model-type ram
    else:
        print('Invalid model or task')

run_inference(model, task)

You selected Tag2Text
You selected multiple images
/encoder/layer/0/crossattention/self/query is tied
/encoder/layer/0/crossattention/self/key is tied
/encoder/layer/0/crossattention/self/value is tied
/encoder/layer/0/crossattention/output/dense is tied
/encoder/layer/0/crossattention/output/LayerNorm is tied
/encoder/layer/0/intermediate/dense is tied
/encoder/layer/0/output/dense is tied
/encoder/layer/0/output/LayerNorm is tied
/encoder/layer/1/crossattention/self/query is tied
/encoder/layer/1/crossattention/self/key is tied
/encoder/layer/1/crossattention/self/value is tied
/encoder/layer/1/crossattention/output/dense is tied
/encoder/layer/1/crossattention/output/LayerNorm is tied
/encoder/layer/1/intermediate/dense is tied
/encoder/layer/1/output/dense is tied
/encoder/layer/1/output/LayerNorm is tied
--------------
pretrained/tag2text_swin_14m.pth
--------------
load checkpoint from pretrained/tag2text_swin_14m.pth
vit: swin_b
2023-06-18 14:48:48.852442: W tensorflow/compiler/